In [2]:
%display latex
Parallelism().set(nproc=8)

This notebook was written under the supervision of Éric Gourgoulhon (LUTH) as part of my physics internship in July 2023.

**Author** : Nicolas Seroux



# Gravitation en $2+1$ dimensions et trou noir BTZ



## Espace\-temps anti\-de Sitter



#### Définitions préliminaires



On commence par définir l'espace temps anti\-de Sitter à trois dimensions comme une sous variété $\mathbb{R}^{2,2}$.

On distinguera l'espace-temps $\mathrm{AdS}_{2+1}\approx\mathrm{SL}_2(\mathbb{R})\approx\mathbb{S}^1\times\mathbb{R}^2$ de son recouvrement universel $\widetilde{\mathrm{Ads}}_{2+1}\approx\mathbb{R}^3$.


In [3]:
AdS = Manifold(3, 'AdS', latex_name=r'\mathrm{AdS}_{2+1}', structure='Lorentzian')
UAdS = Manifold(3, 'UAdS', latex_name=r'\widetilde{\mathrm{AdS}}_{2+1}', structure='Lorentzian')

Les symétries des espaces anti-de Sitter permettent de considérer des coordonnées de type sphérique :

In [4]:
X_AdS.<t,r,ph> = AdS.chart(r't r:(0,+oo) ph:(-pi,pi):\varphi:periodic')
X_UAdS.<t,r,ph> = UAdS.chart(r't r:(0,+oo) ph:\varphi')

On introduit l'espace vectoriel $\mathbb{R}^{2,2}$ comme une variété pseudo\-riemannienne munie de coordonnées cartésiennes et sphériques :


In [5]:
R22 = Manifold(4, 'R22', r'\mathbb{R}^{2,2}', structure='pseudo-Riemannian', signature=0, metric_name='eta', metric_latex_name=r'\eta')

X_Cart.<u,v,x,y> = R22.chart()
F_Cart = X_Cart.frame()

X_Sph.<u,v,r,ph> = R22.chart(r'u v r:(0,+oo) ph:(-pi,pi):\varphi:periodic')
F_Sph = X_Sph.frame()

trans_Sph_to_Cart = X_Sph.transition_map(X_Cart, [u, v, r*cos(ph),r*sin(ph)], restrictions2=(x^2+y^2!=0))
trans_Sph_to_Cart.set_inverse(u, v, sqrt(x^2+y^2),2*arctan(y/(sqrt(x^2+y^2)+x)), check=False)

trans_Cart_to_Sph = trans_Sph_to_Cart.inverse()

La métrique $\eta$ sur $\mathbb{R}^{2,2}$ est plate :


In [6]:
eta = R22.metric()

eta[0,0], eta[1,1], eta[2,2], eta[3,3] = -1, -1, 1, 1

eta.display(X_Sph)

eta = -du⊗du - dv⊗dv + dr⊗dr + r^2 dph⊗dph

#### Plongement de $\mathrm{AdS}_{2+1}$ dans $\mathbb{R}^{2,2}$



L'espace $\mathrm{AdS}_{2+1}$ se plonge dans $\mathbb{R}^{2,2}$ sur la sous\-variété $\{(u,v,x,y)\in\mathbb{R}^{2,2}\,|\,-u^2-v^2+x^2+y^2=-\ell^2\}$, i.e. $\{\mathbf{X}\in\mathbb{R}^{2,2}\,|\,\eta(\mathbf{X},\mathbf{X})=-\ell^2\}$, où $\ell$ est un  paramètre qui donne la courbure de $\mathrm{AdS}_{2+1}$.


In [7]:
l = var('l', latex_name=r'\ell')
assume(l>0)

Le plongement est fourni par l'application $\Phi$ :


In [8]:
Phi = AdS.diff_map(R22, {(X_AdS, X_Sph) : [sqrt(r^2+l^2)*cos(t/l), sqrt(r^2+l^2)*sin(t/l), r, ph]},name='Phi', latex_name=r'\Phi')
Phi.display()

Phi: AdS → R22
   (t, r, ph) ↦ (u, v, x, y) = (sqrt(l^2 + r^2)*cos(t/l), sqrt(l^2 + r^2)*sin(t/l), r*cos(ph), r*sin(ph))
   (t, r, ph) ↦ (u, v, r, ph) = (sqrt(l^2 + r^2)*cos(t/l), sqrt(l^2 + r^2)*sin(t/l), r, ph)

On identifie $\mathrm{AdS}_{2+1}$ à l'image de $\Phi$ dans $\mathbb{R}^{2,2}$. On affiche ici la section de $\Phi(\mathrm{AdS}_{2+1})$ dans le plan $y=0$, qui correspond à l'image des points $\varphi=0$ et $\varphi=\pi$. 


In [9]:
graph_hyp = X_AdS.plot(X_Cart, mapping=Phi, ambient_coords=(x,u,v), fixed_coords={ph:0}, 
                    ranges={t:(-pi,pi), r:(0,2)}, number_values=9, 
                    color={t:'grey', r:'grey'}, thickness=1, parameters={l:1}, 
                    label_axes=False)

graph_hyp += X_AdS.plot(X_Cart, mapping=Phi, ambient_coords=(x,u,v), fixed_coords={ph:pi}, 
                    ranges={t:(-pi,pi), r:(0,2)}, number_values=9, 
                    color={t:'grey', r:'grey'}, thickness=1, parameters={l:1}, 
                    label_axes=False)

Phi_u_0, Phi_u_pi = Phi.coord_functions()[0](t,r,0).subs({l:1}), Phi.coord_functions()[0](t,r,pi).subs({l:1})
Phi_v_0, Phi_v_pi = Phi.coord_functions()[1](t,r,0).subs({l:1}), Phi.coord_functions()[1](t,r,pi).subs({l:1})
Phi_x_0, Phi_x_pi = Phi.coord_functions()[2](t,r,0).subs({l:1}), Phi.coord_functions()[2](t,r,pi).subs({l:1})

hyperboloid = parametric_plot3d([Phi_x_0, Phi_u_0, Phi_v_0], (t,-pi,pi), (r,0,2), color=(.8,.8,0.9))
hyperboloid += parametric_plot3d([Phi_x_pi, Phi_u_pi, Phi_v_pi], (t,-pi,pi), (r,0,2), color=(.8,.8,0.9))

graph_hyp += hyperboloid

show(graph_hyp, aspect_ratio=1, axes_labels=['x','u','v'])

Graphics3d Object

La métrique sur $\mathrm{AdS}_{2+1}$ est alors donnée par tiré\-en\-arrière selon $\Phi$ de la métrique plate $\eta$ :


In [10]:
gAdS = AdS.metric(name = 'g_{AdS}', latex_name=r'g_\mathrm{AdS}')
gAdS.set(Phi.pullback(eta))
gAdS.display()

g_{AdS} = -(l^2 + r^2)/l^2 dt⊗dt + l^2/(l^2 + r^2) dr⊗dr + r^2 dph⊗dph

#### Recouvrement universel de $\mathrm{AdS}_{2+1}$



Le recouvrement universel $\widetilde{\mathrm{AdS}}_{2+1}$ de $\mathrm{AdS}_{2+1}$ est obtenu en _déroulant_ la coordonnée $\varphi$. On note $\pi$ la projection de  $\widetilde{\mathrm{AdS}}_{2+1}$ sur $\mathrm{AdS}_{2+1}$ :


In [11]:
Pi = UAdS.diff_map(AdS, [t,r,ph],name='pi', latex_name=r'\pi')
Pi.display()

pi: UAdS → AdS
   (t, r, ph) ↦ (t, r, ph) = (t, r, ph)

On obtient alors une métrique sur $\widetilde{\mathrm{AdS}}_{2+1}$ :


In [12]:
gUAdS = UAdS.metric(name = 'g_{UAdS}', latex_name=r'g_{\widetilde{\mathrm{AdS}}}')

gUAdS.set(Pi.pullback(gAdS))

gUAdS.display()

g_{UAdS} = -(l^2 + r^2)/l^2 dt⊗dt + l^2/(l^2 + r^2) dr⊗dr + r^2 dph⊗dph

## Trou noir BTZ



#### Écriture de la métrique



Le trou noir BTZ est une solution des équations d'Einstein en dimension trois. On introduit donc $\mathscr{M}_{\mathrm{BTZ}}$ une variété lorentzienne à trois dimensions :


In [13]:
M = Manifold(3, 'M_{BTZ}', latex_name = r'\mathscr{M}_\mathrm{BTZ}', structure = 'Lorentzian')
M

3-dimensional Lorentzian manifold M_{BTZ}

La famille de solutions est paramétrée par les rayons $r_+$ et $r_-$ des horizons, grâce auxquels on peut facilement exprimer la masse $m$ et le moment cinétique $J$. La fonction $\alpha(r)$ est un paramètre utile pour la suite.


In [14]:
rp = var('rp', latex_name=r'r_+')
rm = var('rm', latex_name=r'r_-')

assume(l>0)
assume(rp>0)
assume(rm>0)
assume(rm<rp)

m = (rp^2+rm^2)/(l^2)
J = 2*rp*rm/l

alpha(r) = (r^2-rm^2)/(rp^2-rm^2)

On munit la variété de coordonnées adaptées à la symétrie sphérique  de la solution :


In [15]:
X_Sph_BTZ.<t,r,ph> = M.chart(r't r:(0,+oo) ph:(0,2*pi):\varphi:periodic')
F_Sph=X_Sph.frame()

La métrique de $\mathscr{M}_\mathrm{BTZ}$ s'exprime alors :


In [16]:
g = M.metric(name='g', latex_name=r'g')

g[0,0] = m-r^2/l^2
g[1,1] = 1/(-m+r^2/l^2+J^2/(4*r^2))
g[2,2] = r^2
g[0,2] = -J/2

g.display()

g = (-r^2/l^2 + (rm^2 + rp^2)/l^2) dt⊗dt - rm*rp/l dt⊗dph + 1/(r^2/l^2 + rm^2*rp^2/(l^2*r^2) - (rm^2 + rp^2)/l^2) dr⊗dr - rm*rp/l dph⊗dt + r^2 dph⊗dph

#### Solution des équations d'Einstein



Les tenseurs de courbure associés à la métrique $g$ sont aisément calulés : 


In [17]:
Rc = g.ricci()
R = g.ricci_scalar()
G = Rc-(1/2)*R*g
G.set_name('G')

Le calcul du tenseur de Riemann serait superflu, car en dimension $2+1$, toute l'information du tenseur de Riemann est contenue dans le tenseur de Ricci. En d'autres termes, le tenseur de Weyl est identiquement nul :


In [18]:
g.weyl().display()

C(g) = 0

On reconnaît la forme de la métrique dans l'expression du tenseur d'Einstein :


In [19]:
G.display()

G = -(r^2 - rm^2 - rp^2)/l^4 dt⊗dt - rm*rp/l^3 dt⊗dph + r^2/(r^4 - r^2*rm^2 - (r^2 - rm^2)*rp^2) dr⊗dr - rm*rp/l^3 dph⊗dt + r^2/l^2 dph⊗dph

En fait, le tenseur d'Einstein est proportionnel à la métrique $g$ : 
$$G_{\mu\nu}-\frac{1}{\ell^2}g_{\mu\nu}=0,$$

In [20]:
G - (g)/l^2 == 0

True

ce qui signifie que $(\mathscr{M}_{\mathrm{BTZ}}, g)$ est une solution des équations d'Einstein dans le vide avec une constante cosmologique $\Lambda=-\frac{1}{\ell^2}$. 

De manière équivalente, on peut dire que le couple $(\mathscr{M}_{\mathrm{BTZ}}, g)$ forme une _variété d'Einstein_, ce qui signifie que son tenseur de Ricci est proportionnel à la métrique $g$. On a plus précisment :

$$R_{\mu\nu}=2\Lambda g_{\mu\nu}=-\frac{2}{\ell^2}g_{\mu\nu}.$$


In [21]:
Rc == -2*g/l^2

True

#### Construction géométrique de $\mathscr{M}_\mathrm{BTZ}$



Comme toute solution des équations d'Einstein dans le vide en dimension $2+1$, $\mathscr{M}_\mathrm{BTZ}$ est un espace à courbure constante :


In [22]:
R.display()

r(g): M_{BTZ} → ℝ
   (t, r, ph) ↦ -6/l^2

Cela implique que $\mathscr{M}_\mathrm{BTZ}$ est localement isométrique à $\mathrm{AdS}_{2+1}$. Nous allons exhiber $\mathscr{M}_\mathrm{BTZ}$ comme un quotient de $\widetilde{\mathrm{AdS}}_{2+1}$ par l'action proprement discontinue d'un sous\-groupe discret de son groupe d'isométries.


Comme souvent pour étudier un trou noir, il est commode de découper l'espaces en régions séparées par les horizons \(e.g. Schwarzschild, Reissner\-Nordström, Kerr, etc. \). On introduit donc les parties $\mathcal{R}_\mathrm{I}$, $\mathcal{R}_\mathrm{II}$ et $\mathcal{R}_{\mathrm{III}}$ dans $\widetilde{\mathrm{AdS}}_{2+1}$ et $\mathscr{M}_\mathrm{BTZ}$ selon que $r_+<r$, $r_-<r<r_+$, ou $r<r_-$ respectivement :


In [23]:
regI_UAdS = UAdS.open_subset('R_{IUAdS}', latex_name=r'\mathcal{R}_\mathrm{I}^{(\widetilde{\mathrm{AdS}})}', coord_def={X_UAdS : r>rp})
regII_UAdS = UAdS.open_subset('R_{IIUAdS}', latex_name=r'\mathcal{R}_\mathrm{II}^{(\widetilde{\mathrm{AdS}})}', coord_def={X_UAdS : rm<r<rp})
regIII_UAdS = UAdS.open_subset('R_{IIIUAdS}', latex_name=r'\mathcal{R}_\mathrm{III}^{(\widetilde{\mathrm{AdS}})}', coord_def={X_UAdS : r<rm})

In [24]:
regI_BTZ = M.open_subset('R_{IBTZ}', latex_name=r'\mathcal{R}_\mathrm{I}^{(\mathrm{BTZ})}', coord_def={X_Sph_BTZ : r>rp})
regII_BTZ = M.open_subset('R_{IIBTZ}', latex_name=r'\mathcal{R}_\mathrm{II}^{(\mathrm{BTZ})}', coord_def={X_Sph_BTZ : rm<r<rp})
regIII_BTZ = M.open_subset('R_{IIIBTZ}', latex_name=r'\mathcal{R}_\mathrm{III}^{(\mathrm{BTZ})}', coord_def={X_Sph_BTZ : r<rm})

Ces trois régions divisent naturellement $\mathrm{AdS}_{2+1}$ :


In [25]:
graph_hyp_2 = X_AdS.plot(X_Cart, mapping=Phi, ambient_coords=(x,u,v), fixed_coords={ph:0}, 
                    ranges={t:(-pi,pi), r:(0,2)}, number_values=9, 
                    color={t:'grey', r:'grey'}, thickness=1, parameters={l:1}, 
                    label_axes=False)

graph_hyp_2 += X_AdS.plot(X_Cart, mapping=Phi, ambient_coords=(x,u,v), fixed_coords={ph:pi}, 
                    ranges={t:(-pi,pi), r:(0,2)}, number_values=9, 
                    color={t:'grey', r:'grey'}, thickness=2, parameters={l:1}, 
                    label_axes=False)

Phi_u_0, Phi_u_pi = Phi.coord_functions()[0](t,r,0).subs({l:1}), Phi.coord_functions()[0](t,r,pi).subs({l:1})
Phi_v_0, Phi_v_pi = Phi.coord_functions()[1](t,r,0).subs({l:1}), Phi.coord_functions()[1](t,r,pi).subs({l:1})
Phi_x_0, Phi_x_pi = Phi.coord_functions()[2](t,r,0).subs({l:1}), Phi.coord_functions()[2](t,r,pi).subs({l:1})

hyperboloid_2 = parametric_plot3d([Phi_x_0, Phi_u_0, Phi_v_0], (t,-pi,pi), (r,0,.5), color=(.2,.2,.2))
hyperboloid_2 += parametric_plot3d([Phi_x_pi, Phi_u_pi, Phi_v_pi], (t,-pi,pi), (r,0,.5), color=(.2,.2,.2))
hyperboloid_2 += parametric_plot3d([Phi_x_0, Phi_u_0, Phi_v_0], (t,-pi,pi), (r,.5,1), color=(.2,.2,0.5))
hyperboloid_2 += parametric_plot3d([Phi_x_pi, Phi_u_pi, Phi_v_pi], (t,-pi,pi), (r,.5,1), color=(.2,.2,.5))
hyperboloid_2 += parametric_plot3d([Phi_x_0, Phi_u_0, Phi_v_0], (t,-pi,pi), (r,1,2), color=(.8,.8,0.9))
hyperboloid_2 += parametric_plot3d([Phi_x_pi, Phi_u_pi, Phi_v_pi], (t,-pi,pi), (r,1,2), color=(.8,.8,0.9))

graph_hyp_2 += hyperboloid_2

show(graph_hyp_2, aspect_ratio=1, axes_labels=['x','u','v'])

Graphics3d Object

On introduit de plus une projection naturelle de $\widetilde{\mathrm{AdS}}_{2+1}$ sur $\mathscr{M}_\mathrm{BTZ}$ :



In [26]:
piBTZ = UAdS.diff_map(M, [t,r,ph],name='pi_{BTZ}', latex_name=r'\pi_\mathrm{BTZ}')
piBTZ.display()

pi_{BTZ}: UAdS → M_{BTZ}
   (t, r, ph) ↦ (t, r, ph) = (t, r, ph)

Cette identification donne aussi naturellement un revêtement par $\mathcal{R}_\mathrm{I}^{(\widetilde{\mathrm{AdS}})}$ , $\mathcal{R}_\mathrm{II}^{(\widetilde{\mathrm{AdS}})}$, $\mathcal{R}_\mathrm{III}^{(\widetilde{\mathrm{AdS}})}$  des régions $\mathcal{R}_\mathrm{I}^{(\mathrm{BTZ})}$, $\mathcal{R}_\mathrm{II}^{(\mathrm{BTZ})}$, et $\mathcal{R}_\mathrm{III}^{(\mathrm{BTZ})}$  de $\mathscr{M}_\mathrm{BTZ}$. 



On définit sur chaque région $\mathcal{R}_\mathrm{I}^{(\widetilde{\mathrm{AdS}})}$ , $\mathcal{R}_\mathrm{II}^{(\widetilde{\mathrm{AdS}})}$, $\mathcal{R}_\mathrm{III}^{(\widetilde{\mathrm{AdS}})}$ de $\widetilde{\mathrm{AdS}}_{2+1}$ un plongement $\Psi_\mathrm{I}$, $\Psi_\mathrm{II}$, $\Psi_\mathrm{III}$  vers la partie de $\mathbb{R}^{2,2}$ correspondant à $\mathrm{AdS}_{2+1}$ :


In [27]:
PsiI = regI_UAdS.diff_map(R22, 
                          [l*sqrt(alpha(r))*cosh(rp*ph/l-rm*t/l^2),
                           l*sqrt(alpha(r)-1)*sinh(rp*t/l^2-rm*ph/l),
                           l*sqrt(alpha(r))*sinh(rp*ph/l-rm*t/l^2),
                          l*sqrt(alpha(r)-1)*cosh(rp*t/l^2-rm*ph/l)]
                          ,name='Psi_I', latex_name=r'\Psi_\mathrm{I}')

PsiII = regII_UAdS.diff_map(R22, 
                          [l*sqrt(alpha(r))*cosh(rp*ph/l-rm*t/l^2),
                           -l*sqrt(1-alpha(r))*cosh(rp*t/l^2-rm*ph/l),
                           l*sqrt(alpha(r))*sinh(rp*ph/l-rm*t/l^2),
                          -l*sqrt(1-alpha(r))*sinh(rp*t/l^2-rm*ph/l)]
                          ,name='Psi_II', latex_name=r'\Psi_\mathrm{II}')

PsiIII = regIII_UAdS.diff_map(R22, 
                          [l*sqrt(-alpha(r))*sinh(rp*ph/l-rm*t/l^2),
                           -l*sqrt(1-alpha(r))*cosh(rp*t/l^2-rm*ph/l),
                           l*sqrt(-alpha(r))*cosh(rp*ph/l-rm*t/l^2),
                          -l*sqrt(1-alpha(r))*sinh(rp*t/l^2-rm*ph/l)]
                          ,name='Psi_III', latex_name=r'\Psi_\mathrm{III}')

Par exemple, $\Psi_\mathrm{I}$ est donnée par :


In [28]:
PsiI.display(X_UAdS.restrict(regI_UAdS), X_Cart)

Psi_I: R_{IUAdS} → R22
   (t, r, ph) ↦ (u, v, x, y) = (l*sqrt(-(r^2 - rm^2)/(rm^2 - rp^2))*cosh(ph*rp/l - rm*t/l^2), l*sqrt(-(r^2 - rm^2)/(rm^2 - rp^2) - 1)*sinh(-ph*rm/l + rp*t/l^2), l*sqrt(-(r^2 - rm^2)/(rm^2 - rp^2))*sinh(ph*rp/l - rm*t/l^2), l*sqrt(-(r^2 - rm^2)/(rm^2 - rp^2) - 1)*cosh(-ph*rm/l + rp*t/l^2))

Par tiré\-en\-arrière de $\eta$, on obtient alors sur chaque région $\mathcal{R}_\mathrm{I}^{(\widetilde{\mathrm{AdS}})}$ , $\mathcal{R}_\mathrm{II}^{(\widetilde{\mathrm{AdS}})}$, $\mathcal{R}_\mathrm{III}^{(\widetilde{\mathrm{AdS}})}$ de $\widetilde{\mathrm{AdS}}_{2+1}$ une métrique :


In [29]:
PsiI.pullback(eta).display()

Psi_I^*(eta) = -(r^2 - rm^2 - rp^2)/l^2 dt⊗dt - rm*rp/l dt⊗dph + l^2*r^2/(r^4 - r^2*rm^2 - (r^2 - rm^2)*rp^2) dr⊗dr - rm*rp/l dph⊗dt + r^2 dph⊗dph

In [30]:
PsiII.pullback(eta).display()

Psi_II^*(eta) = -(r^2 - rm^2 - rp^2)/l^2 dt⊗dt - rm*rp/l dt⊗dph + l^2*r^2/(r^4 - r^2*rm^2 - (r^2 - rm^2)*rp^2) dr⊗dr - rm*rp/l dph⊗dt + r^2 dph⊗dph

In [31]:
PsiIII.pullback(eta).display()

Psi_III^*(eta) = -(r^2 - rm^2 - rp^2)/l^2 dt⊗dt - rm*rp/l dt⊗dph + l^2*r^2/(r^4 - r^2*rm^2 - (r^2 - rm^2)*rp^2) dr⊗dr - rm*rp/l dph⊗dt + r^2 dph⊗dph

Ces métriques correspondent dans chaque région au tiré\-en\-arrière sur $\widetilde{\mathrm{AdS}}_{2+1}$ de la métrique $g$ de $\mathscr{M}_\mathrm{BTZ}$ par $\pi_{\mathrm{BTZ}}$ :



In [32]:
piBTZ.pullback(g).display()

pi_{BTZ}^*(g) = -(r^2 - rm^2 - rp^2)/l^2 dt⊗dt - rm*rp/l dt⊗dph + l^2*r^2/(r^4 - r^2*rm^2 - (r^2 - rm^2)*rp^2) dr⊗dr - rm*rp/l dph⊗dt + r^2 dph⊗dph

---



Dans ces coordonnées, le passage de $\widetilde{\mathrm{AdS}}_{2+1}$ à $\mathscr{M}_\mathrm{BTZ}$ correspond à l'_enroulement_ selon $\varphi$, i.e. au quotient par un groupe discret engendré par le vecteur $\partial_\varphi$ :


In [33]:
regI_UAdS.default_frame()[2]

Vector field ∂/∂ph on the Open subset R_{IUAdS} of the 3-dimensional Lorentzian manifold UAdS

Le poussé\-en\-avant de $\partial_\varphi$ dans $\mathbb{R}^{2,2}$ est donné par $\xi=\Psi_*\partial_\varphi$ :


In [34]:
xi = PsiI.pushforward(regI_UAdS.default_frame()[2])
xi.display()

Psi_I_*(∂/∂ph) = -(rp*cosh(rm*t/l^2)*sinh(ph*rp/l) - rp*cosh(ph*rp/l)*sinh(rm*t/l^2))*sqrt(r + rm)*sqrt(r - rm)*sqrt(rm + rp)*sqrt(-rm + rp)/(rm^2 - rp^2) ∂/∂u + (rm*cosh(ph*rm/l)*cosh(rp*t/l^2) - rm*sinh(ph*rm/l)*sinh(rp*t/l^2))*sqrt(r + rp)*sqrt(r - rp)*sqrt(rm + rp)*sqrt(-rm + rp)/(rm^2 - rp^2) ∂/∂v - (rp*cosh(ph*rp/l)*cosh(rm*t/l^2) - rp*sinh(ph*rp/l)*sinh(rm*t/l^2))*sqrt(r + rm)*sqrt(r - rm)*sqrt(rm + rp)*sqrt(-rm + rp)/(rm^2 - rp^2) ∂/∂x - (rm*cosh(rp*t/l^2)*sinh(ph*rm/l) - rm*cosh(ph*rm/l)*sinh(rp*t/l^2))*sqrt(r + rp)*sqrt(r - rp)*sqrt(rm + rp)*sqrt(-rm + rp)/(rm^2 - rp^2) ∂/∂y

Ce vecteur correspond dans $\mathbb{R}^{2,2}$ à :

$$
\xi=\frac{r_+}{\ell}(x\partial_u+u\partial_x)-\frac{r_-}{\ell}(y\partial_v+v\partial_y).
$$

On reconnaît une combinaison linéaire d'éléments de $\mathfrak{so}(2,2)$ — le groupe de symétries d'$\mathrm{AdS}_{2+1}$ étant $\mathrm{SO}(2,2)$ — qui génèrent les transformation spéciales de Lorentz dans les plans $(u,x)$ et $(v,y)$.

